In [1]:
# !pip uninstall transformers -y
# !pip install transformers
# !pip install transformers[sentencepiece] datasets sacrebleu rouge_score py7zr -q
# !pip install accelerate -U
# !pip install evaluate
# !pip install tensorrt
# !pip install tensorflow
# !pip install ipywidgets
# !pip install plotly
#!pip install nbformat

import os
os.environ["TOKENIZERS_PARALLELISM"] = "false"
os.environ["PROTOCOL_BUFFERS_PYTHON_IMPLEMENTATION"]="python"

In [2]:
import pandas as pd
import numpy as np 
import gc

# visualization libraries.
import plotly.graph_objects as go 

# Dataset packages.
from datasets import load_dataset
from datasets.dataset_dict import DatasetDict, Dataset
import datasets

# transformer packages.
from transformers.tokenization_utils import BatchEncoding
from transformers import AutoTokenizer, AutoModelForSeq2SeqLM



In [3]:
# Configuring Pandas to exhibit larger columns.
pd.set_option('display.max_colwidth', 1000)

# Dataset explorations.

In [4]:
def count_box_plot(count_df: pd.DataFrame,
                   height: int,
                   width: int,
                   plot_name: str,
                   want_legend: bool = True,
                   ):
    """ 
    
    """
    for col_name in count_df.columns:
        data = go.Box(
            y = count_df[col_name],
            name = "Box Plot",
            boxmean=True,
            line_color= '#d500ff'
        )
        fig = go.Figure(data = data)

        # Update the layout.
        fig.update_layout(
            title={'text': f'<b>Word Count<br>{plot_name}<sup><i>&nbsp;&nbsp;&nbsp;&nbsp;{col_name}</i></sup></b>',
                   'x': .025, 'xanchor': 'left'},
            margin=dict(t=100),
            showlegend=want_legend,
            template = 'plotly_dark',
            height=height, width=width
        )
        fig.update_yaxes(title_text=f"<b>Words count</b>", showgrid=False)
        fig.update_xaxes(title_text=f"", showgrid=False)

        fig.show()

In [5]:

dataset = load_dataset("ccdv/arxiv-summarization")
dataset

/home/pavithra/projects/Natural-Language-Processing/venv_text_summarizaition/lib/python3.8/site-packages/datasets/load.py:1486: FutureWarning: The repository for ccdv/arxiv-summarization contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/ccdv/arxiv-summarization
You can avoid this message in future by passing the argument `trust_remote_code=True`.
Passing `trust_remote_code=True` will be mandatory to load this dataset from the next major release of `datasets`.
  warnings.warn(


Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

DatasetDict({
    train: Dataset({
        features: ['article', 'abstract'],
        num_rows: 203037
    })
    validation: Dataset({
        features: ['article', 'abstract'],
        num_rows: 6436
    })
    test: Dataset({
        features: ['article', 'abstract'],
        num_rows: 6440
    })
})

In [10]:
# getting the variables.
categorical_columns = dataset["train"].column_names
#categorical_columns = ['article', 'abstract']

In [7]:
# find if there any null values.
data_train = pd.DataFrame(dataset["train"])
print(data_train.isna().sum())


# check the data type of the features.
print(data_train.dtypes)

data_train.head()

article     0
abstract    0
dtype: int64
article     object
abstract    object
dtype: object


article  \
0  additive models @xcite provide an important family of models for semiparametric regression or classification . some reasons for the success of additive models are their increased flexibility when compared to linear or generalized linear models and their increased interpretability when compared to fully nonparametric models . \n it is well - known that good estimators in additive models are in general less prone to the curse of high dimensionality than good estimators in fully nonparametric models . \n many examples of such estimators belong to the large class of regularized kernel based methods over a reproducing kernel hilbert space @xmath0 , see e.g. @xcite . in the last years \n many interesting results on learning rates of regularized kernel based models for additive models have been published when the focus is on sparsity and when the classical least squares loss function is used , see e.g. @xcite , @xcite , @xcite , @xcite , @xcite , @xcite and the references therein . of cou...   
1  the leptonic decays of a charged pseudoscalar meson @xmath7 are processes of the type @xmath8 , where @xmath9 , @xmath10 , or @xmath11 . because no strong interactions are present in the leptonic final state @xmath12 , such decays provide a clean way to probe the complex , strong interactions that bind the quark and antiquark within the initial - state meson . in these decays , strong interaction effects can be parametrized by a single quantity , @xmath13 , the pseudoscalar meson decay constant . \n the leptonic decay rate can be measured by experiment , and the decay constant can be determined by the equation ( ignoring radiative corrections ) @xmath14 where @xmath15 is the fermi coupling constant , @xmath16 is the cabibbo - kobayashi - maskawa ( ckm ) matrix  @xcite element , @xmath17 is the mass of the meson , and @xmath18 is the mass of the charged lepton . \n the quantity @xmath13 describes the amplitude for the @xmath19 and @xmath20-quarks within the @xmath21 to have zero sep...   
2  the transport properties of nonlinear non - equilibrium dynamical systems are far from well - understood@xcite . \n consider in particular so - called ratchet systems which are asymmetric periodic potentials where an ensemble of particles experience directed transport@xcite . \n the origins of the interest in this lie in considerations about extracting useful work from unbiased noisy fluctuations as seems to happen in biological systems@xcite . \n recently attention has been focused on the behavior of deterministic chaotic ratchets@xcite as well as hamiltonian ratchets@xcite . \n chaotic systems are defined as those which are sensitively dependent on initial conditions . whether chaotic or not , the behavior of nonlinear systems  including the transition from regular to chaotic behavior  is in general sensitively dependent on the parameters of the system . \n that is , the phase - space structure is usually relatively complicated , consisting of stability islands embedded in chaoti...   
3  studies of laser beams propagating through turbulent atmospheres are important for many applications such as remote sensing , tracking , and long - distance optical communications . \n howerver , fully coherent laser beams are very sensitive to fluctuations of the atmospheric refractive index . \n the initially coherent laser beam acquires some properties of gaussian statistics in course of its propagation through the turbulence . as a result , the noise / signal ratio approaches unity for long - distance propagation . \n ( see , for example , refs.@xcite-@xcite ) . \n this unfavourable effect limits the performance of communication channels . to mitigate this negative effect \n the use of partially ( spatially ) coherent beams was proposed . \n the coherent laser beam can be transformed into a partially coherent beam by means of a phase diffuser placed near the exit aperture . \n this diffuser introduces an additional phase ( randomly varying in space a

In [11]:
# Count the number of words in each content and headline.
words_count_df = pd.DataFrame()
for col_name in categorical_columns:
    words_count_df[col_name] = data_train[col_name].apply(lambda row: len(str(row).split(" ")))

words_count_df.head()

article  abstract
0     4662       152
1     3500        63
2     5579       268
3     3925        84
4     9720       154

In [12]:
count_box_plot(words_count_df, 800, 800, plot_name="Train data words count")